In [1]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors
from mpl_toolkits.axes_grid1 import make_axes_locatable
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

C:\Users\duval\AppData\Local\Temp\ipykernel_4036\3779468937.py:1: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [2]:
DATA_DIR = 'data/'

In [3]:
olympics_data = pd.read_csv(DATA_DIR + 'dataset_olympics.csv')
noc_regions = pd.read_csv(DATA_DIR + 'noc_region.csv')
athletes = pd.read_csv(DATA_DIR +'dataset_olympics.csv')
gdf_world = gpd.read_file(DATA_DIR +'countries.geojson')
noc_to_country = pd.Series(noc_regions.reg.values, index=noc_regions.noc_region).to_dict()

In [4]:
olympics_data['Medal'] = olympics_data['Medal'].fillna('None')

In [5]:
winter_olympics = olympics_data[olympics_data['Season'] == 'Winter']
summer_olympics = olympics_data[olympics_data['Season'] == 'Summer']
winter_olympics = winter_olympics.sort_values(by='Year')
summer_olympics = summer_olympics.sort_values(by='Year')


#### Medals

In [38]:
# Group the data by Year, Season, Team, and Medal and count the occurrences
medal_count = olympics_data.groupby(['Year', 'Season', 'Medal','NOC'])[['Medal']].count()

# Rename the 'Medal' column to 'Count'
medal_count.rename(columns={'Medal': 'Count'}, inplace=True)

# Reset the index to make it a regular DataFrame
medal_count.reset_index(inplace=True)

# Display the resulting DataFrame
display(medal_count.head())

Year  Season   Medal  NOC  Count
0  1896  Summer  Bronze  GBR      1
1  1896  Summer  Bronze  GRE      3
2  1896  Summer  Bronze  USA      1
3  1896  Summer    Gold  GBR      3
4  1896  Summer    Gold  GER      2

In [40]:
df = medal_count

df['Country'] = df['NOC'].map(noc_to_country)
# Group by 'Year', 'Season', 'Team', and 'Medal' and aggregate the 'Count' column
grouped_df = df.groupby(['Year', 'Season','Country', 'Medal', 'NOC']).sum().reset_index()

# Pivot the DataFrame
pivot_df = grouped_df.pivot_table(index=['Year', 'Season', 'Country', 'NOC'], columns='Medal', values='Count', fill_value=0)

pivot_df = pivot_df[['Gold', 'Silver', 'Bronze', 'None']]
# Reset index to make 'Year', 'Season', and 'Team' as columns
pivot_df = pivot_df.reset_index()

# Save the DataFrame to a CSV file
pivot_df.to_csv('medal_distribution.csv', index=False)

print("CSV file 'medal_distribution.csv' has been saved.")


CSV file 'medal_distribution.csv' has been saved.


In [16]:
# Group the medal count DataFrame by Season and Team, count the number of years each team participated, and sort by descending order of years
participation = medal_count.groupby(['Season', 'Team'])[['Year']].nunique().sort_values(by='Year', ascending=False)

# Rename the 'Year' column to 'Years Participated'
participation.rename(columns={'Year': 'Years Participated'}, inplace=True)

# Reset the index to make it a regular DataFrame
participation.reset_index(inplace=True)

In [18]:
# Merge the medal_count and participation DataFrames on Season and Team columns
medal_win_with_years = pd.merge(medal_count, participation, on=['Season', 'Team'], how='left')

# Pivot the medal_win_with_years DataFrame to get a new DataFrame with index as ['Year', 'Season', 'Team', 'Years Participated'],
# columns as 'Medal', and values as 'Count', aggregating the sum of counts, and filling missing values with 0
medal_win_pivot = medal_win_with_years.pivot_table(index=['Year', 'Season', 'Team', 'Years Participated'],
                                                   columns='Medal',
                                                   values='Count',
                                                   aggfunc='sum',
                                                   fill_value=0).reset_index()


Medal  Year  Season                   Team  Years Participated  Bronze  Gold  \
0      1896  Summer                 France                  29       0     0   
1      1896  Summer                Germany                  20       0     2   
2      1896  Summer          Great Britain                  29       1     2   
3      1896  Summer  Great Britain/Germany                   1       0     1   
4      1896  Summer                 Greece                  27       3     1   

Medal  None  Silver  
0         3       1  
1         8       0  
2         5       1  
3         0       0  
4        15       2

### Gender representation

In [48]:
fig, ax = plt.subplots(1, figsize=(15, 9))
ax.set_axis_off()
cmap = plt.cm.viridis
norm = mcolors.Normalize(vmin=0, vmax=1)

divider = make_axes_locatable(ax)
cax = divider.append_axes("right", size="2%", pad=0.05)
sm = plt.cm.ScalarMappable(cmap=cmap, norm=norm)
sm.set_array([])
cbar = plt.colorbar(sm, cax=cax)
cbar.ax.text(5, -0.07, 'No Female Athletes', va='bottom', ha='right', transform=cbar.ax.transAxes, fontsize=15, fontweight='bold')
cbar.ax.text(7, 1.07, 'Equal Female and Male Athletes', va='top', ha='right', transform=cbar.ax.transAxes, fontsize=15, fontweight='bold')

def update(year):
    ax.clear()
    ax.set_axis_off()
    year_athletes = athletes[athletes['Year'] == year]
    unique_athletes = year_athletes.drop_duplicates(subset=['ID', 'NOC', 'Sex'])
    grouped_athletes = unique_athletes.groupby(['NOC', 'Sex']).size().unstack(fill_value=0)
    grouped_athletes['M'] = grouped_athletes.get('M', 0)
    grouped_athletes['F'] = grouped_athletes.get('F', 0)
    grouped_athletes.rename(columns={'M': 'male_count', 'F': 'female_count'}, inplace=True)
    grouped_athletes['female_male_ratio'] = grouped_athletes['female_count'] / (grouped_athletes['male_count'] + grouped_athletes['female_count'])
    grouped_athletes['country'] = grouped_athletes.index.map(map_noc_to_country)
    merged_gdf = gdf_world.merge(grouped_athletes, how='left', left_on='ADMIN', right_on='country')
    merged_gdf.plot(column='female_male_ratio', ax=ax, cmap=cmap, norm=norm, legend=False, 
                    missing_kwds={'color': 'lightgrey'})
    ax.text(0.02, 0.95, str(year), transform=ax.transAxes, fontsize=20, va='top', ha='left', color='red', backgroundcolor='white', fontweight='bold')

#years = sorted(athletes['Year'].unique())
start_year = athletes['Year'].min()  # Assuming this is an Olympic year
years = [year for year in sorted(athletes['Year'].unique()) if (year - start_year) % 4 == 0]

ani = FuncAnimation(fig, update, frames=years, repeat=True, interval=1000, repeat_delay=2000)

plt.show()

HTML(ani.to_jshtml())
#ani.save('animation.mp4', writer='ffmpeg')

<IPython.core.display.Javascript object>

### Performance Data

#### Data filtering from the datascrapped csv file (see datascrapping performance notebook)

In [9]:
file_path = "C:/Users/duval/Documents/EPFL/MA3/Data Viz/olympedia_all_results.csv"

df = pd.read_csv(file_path)
df.columns = df.columns.str.lower()

C:\Users\duval\AppData\Local\Temp\ipykernel_4036\927455467.py:3: DtypeWarning: Columns (9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,26,27,28,29,30,31,32,33,35,36,37,38,39,40,41,42,43,44,45,46,47,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,68,69,70,71,72,73,74,75,76,77,78,79,80,81,83,84,86,87,89,90,91,92,93,94,96,97,98,99,100,101,102,103,104,105,106,107,108,109,110,111,112,113,114,115,116,117,118,119,120,121,122,123,124,125,126,127,128,129,130,131,132,133,134,135,137,138,139,140,141,142,143,144,145,146,147,148,149,150,151,152,153,154,155,156,157,158,159,160,161,162,163,164,165,166,167,168,169,170,171,172,173,174,176,177,178,179,180,181,182,183,184,185,186,187,188,189,192,193,194,195,196,197,198,199,200,201,202,203,204,205,206,207,208,210,211,212,215,216,217,219,220,221,222,223,224,225,226,227,228,229,230,231,232,233,234,235,236,237,239,241,242,243,244,245,246,247,248,249,250,251,252,253,254,255,256,257,258,259,261,262,263,264,265,266,268,269,270,271,272,274,275,276,277,278,279

In [17]:
# Select columns to keep 
main_keywords = ['result_id', 'event_title', 'edition', 'edition_id', 'sport', 'result_date', 'result_location', 'result_participants', 'pos', 'noc']
athlete_keywords = ['athlete', 'competitor', 'gymnast', 'player', 'swimmer', 'competitors', 'team', 'boat', 'cyclist', 'wrestler', 'judoka', 'pentathlete', 'player', 'skater', 'competitor(s)', 'pair']
performance_keywords = ['time', 'k', 'final', 'final round', 'score', 'rank', 'points', 'pts', 'strokes', 'swimming', 'grand prix freestyle', 'penalty points', 'time/margin', 'rank', 'weight', 'final round 3', 'best time', 'time (a)',
                        'adjusted time']


athlete_keywords = [kw.lower() for kw in athlete_keywords]
performance_keywords = [kw.lower() for kw in performance_keywords]

In [18]:

columns_to_keep = main_keywords + athlete_keywords + performance_keywords

df.columns = df.columns.str.lower()

columns_to_keep = [col.lower() for col in columns_to_keep]

existing_columns_to_keep = [col for col in columns_to_keep if col in df.columns]
existing_athlete_keywords = [col for col in athlete_keywords if col in df.columns]
existing_performance_keywords = [col for col in performance_keywords if col in df.columns]

filtered_df = df[existing_columns_to_keep]

In [19]:
# Merge athlete columns
filtered_df['athlete_combined'] = filtered_df[existing_athlete_keywords].apply(lambda row: ', '.join(row.dropna().astype(str)), axis=1)

# Merge performance columns
filtered_df['performance_combined'] = filtered_df[existing_performance_keywords].apply(lambda row: ', '.join(row.dropna().astype(str)), axis=1)

# Drop the past columns
filtered_df.drop(columns=existing_athlete_keywords + existing_performance_keywords, inplace=True)

# Save CSV
filtered_df.to_csv(DATA_DIR + 'data.csv', index=False)

C:\Users\duval\AppData\Local\Temp\ipykernel_4036\2706219998.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['athlete_combined'] = filtered_df[existing_athlete_keywords].apply(lambda row: ', '.join(row.dropna().astype(str)), axis=1)
C:\Users\duval\AppData\Local\Temp\ipykernel_4036\2706219998.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['performance_combined'] = filtered_df[existing_performance_keywords].apply(lambda row: ', '.join(row.dropna().astype(str)), axis=1)
C:\Users